In [7]:
import numpy as np
import pandas as pd
import nltk
# nltk.download('punkt')
import warnings
warnings.filterwarnings('ignore')
from sklearn.preprocessing import LabelEncoder

In [8]:
list_sent=[]
with open('data.txt', encoding="utf8") as f:
    train_lines = f.readlines()
    for line in train_lines:
        line = line.split('__eou__')
        
        for i in range(len(line)):
            line[i] = line[i].strip()
        list_sent.append(line)

text = []
for i in list_sent:
    text.append(i[0])

label = []
for i in list_sent:
    label.append(i[1])
    
labels = []
for i in range(len(label)):
    labels.append(i)

df = pd.DataFrame({"Nội dung văn bản": text, "Chủ đề": label})
df

Nội dung văn bản   Chủ đề
0                                      Nội dung văn bản   Chủ đề
1                                                               
2     Bắn thuốc mê di dời đàn khỉ trong khu dân cư S...  thoi-su
3                                                               
4     Lớp học bằng ván gỗ cũ nát ở vùng cao Lạng Sơn...  thoi-su
...                                                 ...      ...
3670  Cắm trại đón Giáng sinh trong sân bay Singapor...  du-lich
3671                                                            
3672  Saigontourist Group khuyến mại lớn dịp Giáng s...  du-lich
3673                                                            
3674  Lợi ích khi là khách hàng thân thiết của công ...  du-lich

[3675 rows x 2 columns]

In [9]:
num_classes = len(text)

In [10]:
lbl_encoder = LabelEncoder()
lbl_encoder.fit(label)
labels = lbl_encoder.transform(label)

In [11]:
import tensorflow as tf
tf.compat.v1.logging.set_verbosity(tf.compat.v1.logging.ERROR)
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, GlobalAveragePooling1D, Flatten, LSTM, Conv1D, MaxPooling1D, Dropout, Activation
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [12]:
# the size of the vocabulary in the text data
vocab_size = 2000
# size of the vector space in which words will be embedded
embedding_dim = 16
# length of input sequences
max_len = 20
oov_token = "<OOV>"

tokenizer = Tokenizer(num_words=vocab_size, oov_token=oov_token) # adding out of vocabulary token
tokenizer.fit_on_texts(text)
word_index = tokenizer.word_index
sequences = tokenizer.texts_to_sequences(text)

# The “pad_sequences” method is used to make all the training text sequences into the same size
padded_sequences = pad_sequences(sequences, truncating='post', maxlen=max_len)

In [7]:
print(word_index)

{'<OOV>': 1, 'và': 2, 'của': 3, 'trong': 4, 'có': 5, 'người': 6, 'các': 7, 'là': 8, 'được': 9, 'một': 10, 'không': 11, 'cho': 12, 'với': 13, 'năm': 14, 'học': 15, 'khi': 16, 'ở': 17, 'từ': 18, 'để': 19, 'những': 20, 'đến': 21, 'anh': 22, 'công': 23, 'nhiều': 24, 'bệnh': 25, 'tại': 26, 'thể': 27, 'thành': 28, 'đầu': 29, 'đã': 30, 'ảnh': 31, 'nhân': 32, 'sinh': 33, '1': 34, 'này': 35, 'ngày': 36, 'trên': 37, 'về': 38, 'sau': 39, 'đó': 40, 'vào': 41, 'theo': 42, 'ra': 43, 'hơn': 44, 'tôi': 45, 'đồng': 46, 'nhà': 47, 'hai': 48, 'hiện': 49, 'gia': 50, 'số': 51, 'viên': 52, 'trường': 53, 'bị': 54, 'quốc': 55, 'như': 56, 'làm': 57, 'nhất': 58, 'ông': 59, 'phải': 60, 'sẽ': 61, 'trung': 62, 'việc': 63, 'chỉ': 64, 'lại': 65, 'nam': 66, 'động': 67, 'trước': 68, 'sự': 69, 'cũng': 70, 'sĩ': 71, 'nhận': 72, 'bộ': 73, 'cách': 74, 'khách': 75, 'định': 76, 'mới': 77, 'đại': 78, 'cơ': 79, 'tháng': 80, 'điều': 81, 'nói': 82, 'tế': 83, 'nhưng': 84, 'điểm': 85, 'đi': 86, 'thời': 87, 'vì': 88, 'con': 89, 'c

In [8]:
print(sequences)
print(padded_sequences)

[[139, 722, 164, 205], [], [1693, 592, 1085, 570, 1, 553, 1657, 4, 212, 127, 815, 872, 905, 200, 270, 131, 161, 162, 263, 136, 292, 1693, 592, 1085, 342, 553, 1657, 350, 320, 180, 4, 212, 127, 815, 17, 914, 1838, 632, 474, 105, 19, 1, 38, 755, 36, 883, 34, 59, 416, 894, 494, 1636, 159, 708, 854, 474, 105, 12, 96, 388, 618, 570, 1, 553, 1657, 61, 9, 362, 113, 18, 36, 564, 34, 32, 52, 317, 541, 162, 263, 103, 419, 553, 1657, 141, 1, 37, 1020, 1180, 31, 265, 164, 42, 172, 218, 9, 268, 43, 79, 103, 131, 161, 61, 421, 1, 228, 1112, 1666, 369, 1693, 592, 1, 592, 350, 1085, 4, 989, 135, 19, 342, 553, 1657, 16, 1225, 592, 4, 505, 121, 383, 156, 61, 314, 359, 1014, 428, 257, 108, 895, 342, 32, 52, 317, 541, 162, 263, 12, 96, 39, 16, 21, 212, 127, 815, 1016, 419, 59, 221, 632, 565, 499, 1026, 326, 317, 541, 162, 263, 12, 96, 553, 1657, 61, 9, 268, 38, 1538, 199, 715, 67, 351, 1398, 1399, 1429, 499, 727, 803, 1996, 363, 68, 16, 1, 38, 755, 187, 10, 14, 91, 187, 1171, 715, 127, 26, 212, 269, 299, 

In [9]:
model = Sequential()
model.add(Embedding(vocab_size, embedding_dim, input_length=max_len))
model.add(Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
model.add(LSTM(150))
model.add(Dense(16, activation='relu')) # 16 class to categorize data
model.add(Dense(16, activation='relu')) # 2 times, more exactly
model.add(Dense(num_classes, activation='softmax'))

model.compile(loss='sparse_categorical_crossentropy', 
              optimizer='adam', metrics=['accuracy'])


In [10]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 20, 16)            32000     
_________________________________________________________________
conv1d (Conv1D)              (None, 20, 32)            1568      
_________________________________________________________________
lstm (LSTM)                  (None, 150)               109800    
_________________________________________________________________
dense (Dense)                (None, 16)                2416      
_________________________________________________________________
dense_1 (Dense)              (None, 16)                272       
_________________________________________________________________
dense_2 (Dense)              (None, 3675)              62475     
Total params: 208,531
Trainable params: 208,531
Non-trainable params: 0
__________________________________________________

In [11]:
epochs = 400
history = model.fit(padded_sequences, np.array(labels), epochs=epochs)

Epoch 1/400
115/115 [==============================] - 4s 16ms/step - loss: 3.2277 - accuracy: 0.4963
Epoch 2/400
115/115 [==============================] - 2s 16ms/step - loss: 1.6076 - accuracy: 0.4999
Epoch 3/400
115/115 [==============================] - 2s 16ms/step - loss: 1.6094 - accuracy: 0.4999
Epoch 4/400
115/115 [==============================] - 2s 14ms/step - loss: 1.6043 - accuracy: 0.4999
Epoch 5/400
115/115 [==============================] - 2s 14ms/step - loss: 1.5945 - accuracy: 0.4999
Epoch 6/400
115/115 [==============================] - 2s 14ms/step - loss: 1.2471 - accuracy: 0.5420
Epoch 7/400
115/115 [==============================] - 2s 15ms/step - loss: 1.0510 - accuracy: 0.5853
Epoch 8/400
115/115 [==============================] - 2s 17ms/step - loss: 1.0079 - accuracy: 0.6054
Epoch 9/400
115/115 [==============================] - 2s 18ms/step - loss: 0.9171 - accuracy: 0.6294
Epoch 10/400
115/115 [==============================] - 2s 15ms/step - loss: 0.849

In [12]:
# saving model
model.save("model_vietnam.h5")

# implements binary protocols for serializing and de-serializing a Python object structure.
import pickle

# saving tokenizer
with open('tokenizer.pickle', 'wb') as handle:
    pickle.dump(tokenizer, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
#saving label encoder
with open('label_encoder.pickle', 'wb') as ecn_file:
    pickle.dump(lbl_encoder, ecn_file, protocol=pickle.HIGHEST_PROTOCOL)

In [1]:
import random
from difflib import SequenceMatcher
import pickle

def result(inp):
    # load trained model
    model = keras.models.load_model('model_vietnam.h5')

    # load tokenizer object
    with open('tokenizer.pickle', 'rb') as handle:
        tokenizer = pickle.load(handle)
    
    # load label encoder object
    with open('label_encoder.pickle', 'rb') as enc:
        lbl_encoder = pickle.load(enc)

    # parameters
    max_len = 20
    
    result = model.predict(keras.preprocessing.sequence.pad_sequences(tokenizer.texts_to_sequences([inp]),
                                         truncating='post', maxlen=max_len))
    tag = lbl_encoder.inverse_transform([np.argmax(result)])
    new_tag = tag
    print(new_tag)

In [2]:
f = open('news.txt', encoding='utf8')
f = f.read()
f = str(f)
result(f)

NameError: name 'keras' is not defined

In [21]:
from pyvi import ViTokenizer, ViPosTagger
a = ViTokenizer.tokenize(u"Trường đại học bách khoa hà nội")
b = ViPosTagger.postagging(ViTokenizer.tokenize(u"Trường đại học Bách Khoa Hà Nội"))



In [77]:
x = 'Thêm 9.889 ca Covid-19 Trong 9.889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9.882 ca tại 57 tỉnh thành, tăng 364 ca so với hôm qua; 5.163 người khỏi; số tử vong xuống dưới 100 ca, còn 76. Hôm nay, 4.521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa (giảm 221 ca), 5.361 ca cộng đồng (tăng 585 ca). Trong đó, Đăk Lăk giảm 205 ca, Bình Phước giảm 101 ca, Tiền Giang giảm 100 ca; còn TP HCM tăng 219 ca, Bà Rịa Vũng Tàu tăng 171 ca, Cần Thơ tăng 140 ca. Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9.616 ca/ngày. Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15, Long An 8, An Giang và Đồng Nai 7, Tiền Giang và Cần Thơ 6, Tây Ninh và Kiên Giang 5, Sóc Trăng và Bạc Liêu 4, Bình Thuận 3, Đồng Tháp và Vĩnh Long 2, Quảng Ngãi và Cà Mau đều một. Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca. Tổng số ca tử vong tại Việt Nam tính đến nay là 23.761 ca, chiếm tỷ lệ 2,2% so với tổng số ca nhiễm. Đợt dịch thứ 4, số ca nhiễm trong nước là 1.089.411, trong đó 902.683 ca đã được công bố khỏi bệnh. Kể từ đầu dịch đến nay Việt Nam ghi nhận 1.094.514 ca nhiễm, đứng thứ 37/223 quốc gia và vùng lãnh thổ. 2 tỉnh, thành phố không có ca lây nhiễm thứ phát trên địa bàn trong 14 ngày qua: Yên Bái, Bắc Kạn. Các địa phương ghi nhận số nhiễm tích lũy cao trong đợt dịch này: TP HCM 456.372 ca, Bình Dương 248.020, Đồng Nai 82.292, Long An 37.324, Tiền Giang 23.867 ca. Về điều trị, số người khỏi bệnh trong ngày là 5.163. Tổng số ca được điều trị khỏi lên 905.500. Số bệnh nhân nặng đang điều trị là 4.971 ca, trong đó 3.399 thở oxy qua mặt nạ; 978 thở oxy dòng cao HFNC; 128 thở máy không xâm lấn; 458 thở máy xâm lấn và 8 ECMO. Về xét nghiệm, trong 24 giờ qua đã thực hiện 108.677 xét nghiệm cho 188.844 lượt người. Số lượng xét nghiệm từ 27/4 đến nay đã thực hiện 24,9 triệu mẫu cho 65,8 triệu lượt người. Về tiêm chủng, trong ngày 20/11 có 1.298.149 liều vaccine được tiêm. Như vậy, tổng số liều đã được tiêm là 107,8 triệu liều, trong đó tiêm 1 mũi là 66,7 triệu liều, tiêm mũi 2 là 41,1 triệu liều. Bộ Y tế chỉ đạo địa phương và các đơn vị liên quan thực hiện rà soát tất cả những người đi về từ các tỉnh, thành phố có số nhiễm cao (như TP HCM, Bình Dương, Đồng Nai, Long An...). Giám sát, xét nghiệm các trường hợp có nguy cơ cao, nhất là người về từ các địa bàn dịch cấp độ 3, 4; trường hợp có dấu hiệu nghi ngờ nhiễm bệnh; tổ chức cách ly, theo dõi sức khỏe phù hợp và xử lý kịp thời các ổ dịch.'

In [78]:
newstr = x.replace(".", "")
newstr


'Thêm 9889 ca Covid-19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành, tăng 364 ca so với hôm qua; 5163 người khỏi; số tử vong xuống dưới 100 ca, còn 76 Hôm nay, 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa (giảm 221 ca), 5361 ca cộng đồng (tăng 585 ca) Trong đó, Đăk Lăk giảm 205 ca, Bình Phước giảm 101 ca, Tiền Giang giảm 100 ca; còn TP HCM tăng 219 ca, Bà Rịa Vũng Tàu tăng 171 ca, Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15, Long An 8, An Giang và Đồng Nai 7, Tiền Giang và Cần Thơ 6, Tây Ninh và Kiên Giang 5, Sóc Trăng và Bạc Liêu 4, Bình Thuận 3, Đồng Tháp và Vĩnh Long 2, Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca, chiếm tỷ lệ 2,2% so với tổng số ca nhiễm Đợt dịch thứ 4, số ca nhiễm trong nước là 1089411, trong đó 902683 ca đã đượ

In [79]:
newstr = newstr.replace(",", "")
newstr

'Thêm 9889 ca Covid-19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành tăng 364 ca so với hôm qua; 5163 người khỏi; số tử vong xuống dưới 100 ca còn 76 Hôm nay 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa (giảm 221 ca) 5361 ca cộng đồng (tăng 585 ca) Trong đó Đăk Lăk giảm 205 ca Bình Phước giảm 101 ca Tiền Giang giảm 100 ca; còn TP HCM tăng 219 ca Bà Rịa Vũng Tàu tăng 171 ca Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15 Long An 8 An Giang và Đồng Nai 7 Tiền Giang và Cần Thơ 6 Tây Ninh và Kiên Giang 5 Sóc Trăng và Bạc Liêu 4 Bình Thuận 3 Đồng Tháp và Vĩnh Long 2 Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca chiếm tỷ lệ 22% so với tổng số ca nhiễm Đợt dịch thứ 4 số ca nhiễm trong nước là 1089411 trong đó 902683 ca đã được công bố khỏi bệnh K

In [80]:
newstr = newstr.replace(":", " ")
newstr

'Thêm 9889 ca Covid-19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành tăng 364 ca so với hôm qua; 5163 người khỏi; số tử vong xuống dưới 100 ca còn 76 Hôm nay 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa (giảm 221 ca) 5361 ca cộng đồng (tăng 585 ca) Trong đó Đăk Lăk giảm 205 ca Bình Phước giảm 101 ca Tiền Giang giảm 100 ca; còn TP HCM tăng 219 ca Bà Rịa Vũng Tàu tăng 171 ca Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15 Long An 8 An Giang và Đồng Nai 7 Tiền Giang và Cần Thơ 6 Tây Ninh và Kiên Giang 5 Sóc Trăng và Bạc Liêu 4 Bình Thuận 3 Đồng Tháp và Vĩnh Long 2 Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca chiếm tỷ lệ 22% so với tổng số ca nhiễm Đợt dịch thứ 4 số ca nhiễm trong nước là 1089411 trong đó 902683 ca đã được công bố khỏi bệnh K

In [81]:
newstr = newstr.replace(";", " ")
newstr

'Thêm 9889 ca Covid-19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành tăng 364 ca so với hôm qua  5163 người khỏi  số tử vong xuống dưới 100 ca còn 76 Hôm nay 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa (giảm 221 ca) 5361 ca cộng đồng (tăng 585 ca) Trong đó Đăk Lăk giảm 205 ca Bình Phước giảm 101 ca Tiền Giang giảm 100 ca  còn TP HCM tăng 219 ca Bà Rịa Vũng Tàu tăng 171 ca Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15 Long An 8 An Giang và Đồng Nai 7 Tiền Giang và Cần Thơ 6 Tây Ninh và Kiên Giang 5 Sóc Trăng và Bạc Liêu 4 Bình Thuận 3 Đồng Tháp và Vĩnh Long 2 Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca chiếm tỷ lệ 22% so với tổng số ca nhiễm Đợt dịch thứ 4 số ca nhiễm trong nước là 1089411 trong đó 902683 ca đã được công bố khỏi bệnh K

In [82]:
newstr = newstr.replace("(", " ")
newstr

'Thêm 9889 ca Covid-19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành tăng 364 ca so với hôm qua  5163 người khỏi  số tử vong xuống dưới 100 ca còn 76 Hôm nay 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa  giảm 221 ca) 5361 ca cộng đồng  tăng 585 ca) Trong đó Đăk Lăk giảm 205 ca Bình Phước giảm 101 ca Tiền Giang giảm 100 ca  còn TP HCM tăng 219 ca Bà Rịa Vũng Tàu tăng 171 ca Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15 Long An 8 An Giang và Đồng Nai 7 Tiền Giang và Cần Thơ 6 Tây Ninh và Kiên Giang 5 Sóc Trăng và Bạc Liêu 4 Bình Thuận 3 Đồng Tháp và Vĩnh Long 2 Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca chiếm tỷ lệ 22% so với tổng số ca nhiễm Đợt dịch thứ 4 số ca nhiễm trong nước là 1089411 trong đó 902683 ca đã được công bố khỏi bệnh K

In [83]:
newstr = newstr.replace("-", " ")


In [84]:
newstr

'Thêm 9889 ca Covid 19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành tăng 364 ca so với hôm qua  5163 người khỏi  số tử vong xuống dưới 100 ca còn 76 Hôm nay 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa  giảm 221 ca) 5361 ca cộng đồng  tăng 585 ca) Trong đó Đăk Lăk giảm 205 ca Bình Phước giảm 101 ca Tiền Giang giảm 100 ca  còn TP HCM tăng 219 ca Bà Rịa Vũng Tàu tăng 171 ca Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15 Long An 8 An Giang và Đồng Nai 7 Tiền Giang và Cần Thơ 6 Tây Ninh và Kiên Giang 5 Sóc Trăng và Bạc Liêu 4 Bình Thuận 3 Đồng Tháp và Vĩnh Long 2 Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca chiếm tỷ lệ 22% so với tổng số ca nhiễm Đợt dịch thứ 4 số ca nhiễm trong nước là 1089411 trong đó 902683 ca đã được công bố khỏi bệnh K

In [85]:
newstr = newstr.replace(")", "")

In [87]:
newstr

'Thêm 9889 ca Covid 19 Trong 9889 ca nhiễm mới Bộ Y tế công bố tối 21/11 có 9882 ca tại 57 tỉnh thành tăng 364 ca so với hôm qua  5163 người khỏi  số tử vong xuống dưới 100 ca còn 76 Hôm nay 4521 ca được phát hiện ở khu cách ly hoặc khu đã được phong tỏa  giảm 221 ca 5361 ca cộng đồng  tăng 585 ca Trong đó Đăk Lăk giảm 205 ca Bình Phước giảm 101 ca Tiền Giang giảm 100 ca  còn TP HCM tăng 219 ca Bà Rịa Vũng Tàu tăng 171 ca Cần Thơ tăng 140 ca Trung bình số ca nhiễm mới trong nước ghi nhận trong 7 ngày qua qua 9616 ca/ngày Trong ngày ghi nhận 76 ca tử vong tại Bình Dương 15 Long An 8 An Giang và Đồng Nai 7 Tiền Giang và Cần Thơ 6 Tây Ninh và Kiên Giang 5 Sóc Trăng và Bạc Liêu 4 Bình Thuận 3 Đồng Tháp và Vĩnh Long 2 Quảng Ngãi và Cà Mau đều một Trung bình số tử vong ghi nhận trong 7 ngày qua 97 ca Tổng số ca tử vong tại Việt Nam tính đến nay là 23761 ca chiếm tỷ lệ 22% so với tổng số ca nhiễm Đợt dịch thứ 4 số ca nhiễm trong nước là 1089411 trong đó 902683 ca đã được công bố khỏi bệnh Kể 